In [ ]:
import gradio as gr
import requests
import os
import time
import re
import logging
import tempfile
import folium
import concurrent.futures
import torch
from PIL import Image
from datetime import datetime
from transformers import pipeline, AutoModelForSpeechSeq2Seq, AutoProcessor
from googlemaps import Client as GoogleMapsClient
from gtts import gTTS
from diffusers import StableDiffusionPipeline
from langchain_openai import OpenAIEmbeddings, ChatOpenAI
from langchain_pinecone import PineconeVectorStore
from langchain.prompts import PromptTemplate
from langchain.chains import RetrievalQA
from langchain.chains.conversation.memory import ConversationBufferWindowMemory
from huggingface_hub import login
from transformers.models.speecht5.number_normalizer import EnglishNumberNormalizer
from parler_tts import ParlerTTSForConditionalGeneration
from transformers import AutoTokenizer, AutoFeatureExtractor, set_seed
from scipy.io.wavfile import write as write_wav
from pydub import AudioSegment
from string import punctuation
import librosa
from pathlib import Path
import torchaudio
import numpy as np
from transformers import AutoModelForCausalLM, AutoTokenizer, pipeline


# Neo4j imports
from langchain.chains import GraphCypherQAChain
from langchain_community.graphs import Neo4jGraph
from langchain_community.document_loaders import HuggingFaceDatasetLoader
from langchain_text_splitters import CharacterTextSplitter
from langchain_experimental.graph_transformers import LLMGraphTransformer
from langchain_core.prompts import ChatPromptTemplate
from langchain_core.pydantic_v1 import BaseModel, Field
from langchain_core.messages import AIMessage, HumanMessage
from langchain_core.output_parsers import StrOutputParser
from langchain_core.runnables import RunnableBranch, RunnableLambda, RunnableParallel, RunnablePassthrough
from serpapi.google_search import GoogleSearch

#Parler TTS v1 Modules

import os
import re
import tempfile
import soundfile as sf
from string import punctuation
from pydub import AudioSegment
from transformers import AutoTokenizer, AutoFeatureExtractor



#API AutoDate Fix Up
def get_current_date1():
    return datetime.now().strftime("%Y-%m-%d")

# Usage
current_date1 = get_current_date1()



# Set environment variables for CUDA
os.environ['PYTORCH_USE_CUDA_DSA'] = '1'
os.environ['CUDA_LAUNCH_BLOCKING'] = '1'


hf_token = os.getenv("HF_TOKEN")
if hf_token is None:
    print("Please set your Hugging Face token in the environment variables.")
else:
    login(token=hf_token)

logging.basicConfig(level=logging.DEBUG)


embeddings = OpenAIEmbeddings(api_key=os.environ['OPENAI_API_KEY'])


#Initialization

# Initialize the models
def initialize_phi_model():
    model = AutoModelForCausalLM.from_pretrained(
        "microsoft/Phi-3.5-mini-instruct",
        device_map="cuda",
        torch_dtype="auto",
        trust_remote_code=True,
    )
    tokenizer = AutoTokenizer.from_pretrained("microsoft/Phi-3.5-mini-instruct")
    return pipeline("text-generation", model=model, tokenizer=tokenizer)

def initialize_gpt_model():
    return ChatOpenAI(api_key=os.environ['OPENAI_API_KEY'], temperature=0, model='gpt-4o')

# Initialize both models
phi_pipe = initialize_phi_model()
gpt_model = initialize_gpt_model()


# Existing embeddings and vector store for GPT-4o
gpt_embeddings = OpenAIEmbeddings(api_key=os.environ['OPENAI_API_KEY'])
gpt_vectorstore = PineconeVectorStore(index_name="radarfinaldata08192024", embedding=gpt_embeddings)
gpt_retriever = gpt_vectorstore.as_retriever(search_kwargs={'k': 5})

# New vector store setup for Phi-3.5
phi_embeddings = OpenAIEmbeddings(api_key=os.environ['OPENAI_API_KEY'])
phi_vectorstore = PineconeVectorStore(index_name="phivector08252024", embedding=phi_embeddings)
phi_retriever = phi_vectorstore.as_retriever(search_kwargs={'k': 5})



# Pinecone setup
from pinecone import Pinecone
pc = Pinecone(api_key=os.environ['PINECONE_API_KEY'])

index_name = "radarfinaldata08192024"
vectorstore = PineconeVectorStore(index_name=index_name, embedding=embeddings)
retriever = vectorstore.as_retriever(search_kwargs={'k': 5})

chat_model = ChatOpenAI(api_key=os.environ['OPENAI_API_KEY'], temperature=0, model='gpt-4o')

conversational_memory = ConversationBufferWindowMemory(
    memory_key='chat_history',
    k=10,
    return_messages=True
)

# Prompt templates
def get_current_date():
    return datetime.now().strftime("%B %d, %Y")

current_date = get_current_date()

template1 = f"""As an expert concierge in Birmingham, Alabama, known for being a helpful and renowned guide, I am here to assist you on this sunny bright day of {current_date}. Given the current weather conditions and date, I have access to a plethora of information regarding events, places,sports and activities in Birmingham that can enhance your experience.
If you have any questions or need recommendations, feel free to ask. I have a wealth of knowledge of perennial events in Birmingham and can provide detailed information to ensure you make the most of your time here. Remember, I am here to assist you in any way possible.
Now, let me guide you through some of the exciting events happening today in Birmingham, Alabama:
Address: >>, Birmingham, AL
Time: >>__
Date: >>__
Description: >>__
Address: >>, Birmingham, AL
Time: >>__
Date: >>__
Description: >>__
Address: >>, Birmingham, AL
Time: >>__
Date: >>__
Description: >>__
Address: >>, Birmingham, AL
Time: >>__
Date: >>__
Description: >>__
Address: >>, Birmingham, AL
Time: >>__
Date: >>__
Description: >>__
If you have any specific preferences or questions about these events or any other inquiries, please feel free to ask. Remember, I am here to ensure you have a memorable and enjoyable experience in Birmingham, AL.
It was my pleasure!
{{context}}
Question: {{question}}
Helpful Answer:"""

# template2 = f"""As an expert concierge known for being helpful and a renowned guide for Birmingham, Alabama, I assist visitors in discovering the best that the city has to offer. Given today's sunny and bright weather on {current_date}, I am well-equipped to provide valuable insights and recommendations without revealing the locations. I draw upon my extensive knowledge of the area, including perennial events and historical context.
# In light of this, how can I assist you today? Feel free to ask any questions or seek recommendations for your day in Birmingham. If there's anything specific you'd like to know or experience, please share, and I'll be glad to help. Remember, keep the question concise for a quick and accurate response.
# "It was my pleasure!"
# {{context}}
# Question: {{question}}
# Helpful Answer:"""



template2 =f"""Hello there! As your friendly and knowledgeable guide here in Birmingham, Alabama . I'm here to help you discover the best experiences this beautiful city has to offer. It's a bright and sunny day today, {current_date}, and I’m excited to assist you with any insights or recommendations you need.
Whether you're looking for local events, sports ,clubs,concerts etc or just a great place to grab a bite, I've got you covered.Keep your response casual, short and sweet for the quickest response.Don't reveal the location and give the response in a descriptive way, I'm here to help make your time in Birmingham unforgettable!
"It’s always a pleasure to assist you!"
{{context}}
Question: {{question}}
Helpful Answer:"""


QA_CHAIN_PROMPT_1 = PromptTemplate(input_variables=["context", "question"], template=template1)
QA_CHAIN_PROMPT_2 = PromptTemplate(input_variables=["context", "question"], template=template2)

# Neo4j setup
graph = Neo4jGraph(url="neo4j+s://6457770f.databases.neo4j.io",
                    username="neo4j",
                    password="Z10duoPkKCtENuOukw3eIlvl0xJWKtrVSr-_hGX1LQ4"
                    )
# Avoid pushing the graph documents to Neo4j every time
# Only push the documents once and comment the code below after the initial push
# dataset_name = "Pijush2023/birmindata07312024"
# page_content_column = 'events_description'
# loader = HuggingFaceDatasetLoader(dataset_name, page_content_column)
# data = loader.load()

# text_splitter = CharacterTextSplitter(chunk_size=100, chunk_overlap=50)
# documents = text_splitter.split_documents(data)

# llm_transformer = LLMGraphTransformer(llm=chat_model)
# graph_documents = llm_transformer.convert_to_graph_documents(documents)
# graph.add_graph_documents(graph_documents, baseEntityLabel=True, include_source=True)

class Entities(BaseModel):
    names: list[str] = Field(..., description="All the person, organization, or business entities that appear in the text")

entity_prompt = ChatPromptTemplate.from_messages([
    ("system", "You are extracting organization and person entities from the text."),
    ("human", "Use the given format to extract information from the following input: {question}"),
])

entity_chain = entity_prompt | chat_model.with_structured_output(Entities)

def remove_lucene_chars(input: str) -> str:
    return input.translate(str.maketrans({"\\": r"\\", "+": r"\+", "-": r"\-", "&": r"\&", "|": r"\|", "!": r"\!",
                                          "(": r"\(", ")": r"\)", "{": r"\{", "}": r"\}", "[": r"\[", "]": r"\]",
                                          "^": r"\^", "~": r"\~", "*": r"\*", "?": r"\?", ":": r"\:", '"': r'\"',
                                          ";": r"\;", " ": r"\ "}))

def generate_full_text_query(input: str) -> str:
    full_text_query = ""
    words = [el for el in remove_lucene_chars(input).split() if el]
    for word in words[:-1]:
        full_text_query += f" {word}~2 AND"
    full_text_query += f" {words[-1]}~2"
    return full_text_query.strip()

def structured_retriever(question: str) -> str:
    result = ""
    entities = entity_chain.invoke({"question": question})
    for entity in entities.names:
        response = graph.query(
            """CALL db.index.fulltext.queryNodes('entity', $query, {limit:2})
            YIELD node,score
            CALL {
              WITH node
              MATCH (node)-[r:!MENTIONS]->(neighbor)
              RETURN node.id + ' - ' + type(r) + ' -> ' + neighbor.id AS output
              UNION ALL
              WITH node
              MATCH (node)<-[r:!MENTIONS]-(neighbor)
              RETURN neighbor.id + ' - ' + type(r) + ' -> ' +  node.id AS output
            }
            RETURN output LIMIT 50
            """,
            {"query": generate_full_text_query(entity)},
        )
        result += "\n".join([el['output'] for el in response])
    return result

def retriever_neo4j(question: str):
    structured_data = structured_retriever(question)
    logging.debug(f"Structured data: {structured_data}")
    return structured_data

_template = """Given the following conversation and a follow-up question, rephrase the follow-up question to be a standalone question,
in its original language.
Chat History:
{chat_history}
Follow Up Input: {question}
Standalone question:"""

CONDENSE_QUESTION_PROMPT = PromptTemplate.from_template(_template)

def _format_chat_history(chat_history: list[tuple[str, str]]) -> list:
    buffer = []
    for human, ai in chat_history:
        buffer.append(HumanMessage(content=human))
        buffer.append(AIMessage(content=ai))
    return buffer

_search_query = RunnableBranch(
    (
        RunnableLambda(lambda x: bool(x.get("chat_history"))).with_config(
            run_name="HasChatHistoryCheck"
        ),
        RunnablePassthrough.assign(
            chat_history=lambda x: _format_chat_history(x["chat_history"])
        )
        | CONDENSE_QUESTION_PROMPT
        | ChatOpenAI(temperature=0, api_key=os.environ['OPENAI_API_KEY'])
        | StrOutputParser(),
    ),
    RunnableLambda(lambda x : x["question"]),
)

# template = """Answer the question based only on the following context:
# {context}
# Question: {question}
# Use natural language and be concise.
# Answer:"""

template = f"""As an expert concierge known for being helpful and a renowned guide for Birmingham, Alabama, I assist visitors in discovering the best that the city has to offer.I also assist the visitors about various sports and activities. Given today's sunny and bright weather on {current_date}, I am well-equipped to provide valuable insights and recommendations without revealing specific locations. I draw upon my extensive knowledge of the area, including perennial events and historical context.
In light of this, how can I assist you today? Feel free to ask any questions or seek recommendations for your day in Birmingham. If there's anything specific you'd like to know or experience, please share, and I'll be glad to help. Remember, keep the question concise for a quick,short ,crisp and accurate response.
"It was my pleasure!"
{{context}}
Question: {{question}}
Helpful Answer:"""

qa_prompt = ChatPromptTemplate.from_template(template)

chain_neo4j = (
    RunnableParallel(
        {
            "context": _search_query | retriever_neo4j,
            "question": RunnablePassthrough(),
        }
    )
    | qa_prompt
    | chat_model
    | StrOutputParser()
)







phi_custom_template = """
<|system|>
You are a helpful assistant who provides clear, organized, crisp and conversational responses about an events,concerts,sports and all other activities of Birmingham,Alabama .<|end|>
<|user|>
{context}
Question: {question}<|end|>
<|assistant|>
Sure! Here's the information you requested:
"""


def generate_bot_response(history, choice, retrieval_mode, model_choice):
    if not history:
        return

    # Select the model
    selected_model = chat_model if model_choice == "GPT-4o" else phi_pipe

    response, addresses = generate_answer(history[-1][0], choice, retrieval_mode, selected_model)
    history[-1][1] = ""

    for character in response:
        history[-1][1] += character
        yield history  # Stream each character as it is generated
        time.sleep(0.05)  # Add a slight delay to simulate streaming

    yield history  # Final yield with the complete response



def generate_tts_response(response, tts_choice):
    with concurrent.futures.ThreadPoolExecutor() as executor:
        if tts_choice == "Alpha":
            audio_future = executor.submit(generate_audio_elevenlabs, response)
        elif tts_choice == "Beta":
            audio_future = executor.submit(generate_audio_parler_tts, response)
        # elif tts_choice == "Gamma":
        #     audio_future = executor.submit(generate_audio_mars5, response)

        audio_path = audio_future.result()
        return audio_path





import concurrent.futures
# Existing bot function with concurrent futures for parallel processing
def bot(history, choice, tts_choice, retrieval_mode, model_choice):
    # Initialize an empty response
    response = ""

    # Create a thread pool to handle both text generation and TTS conversion in parallel
    with concurrent.futures.ThreadPoolExecutor() as executor:
        # Start the bot response generation in parallel
        bot_future = executor.submit(generate_bot_response, history, choice, retrieval_mode, model_choice)

        # Wait for the text generation to start
        for history_chunk in bot_future.result():
            response = history_chunk[-1][1]  # Update the response with the current state
            yield history_chunk, None  # Stream the text output as it's generated

        # Once text is fully generated, start the TTS conversion
        tts_future = executor.submit(generate_tts_response, response, tts_choice)

        # Get the audio output after TTS is done
        audio_path = tts_future.result()

        # Stream the final text and audio output
        yield history, audio_path







# Modified bot function to separate chatbot response and TTS generation

def generate_bot_response(history, choice, retrieval_mode, model_choice):
    if not history:
        return

    # Select the model
    selected_model = chat_model if model_choice == "GPT-4o" else phi_pipe

    response, addresses = generate_answer(history[-1][0], choice, retrieval_mode, selected_model)
    history[-1][1] = ""

    for character in response:
        history[-1][1] += character
        yield history  # Stream each character as it is generated
        time.sleep(0.05)  # Add a slight delay to simulate streaming

    yield history  # Final yield with the complete response




def generate_audio_after_text(response, tts_choice):
    # Generate TTS audio after text response is completed
    with concurrent.futures.ThreadPoolExecutor() as executor:
        tts_future = executor.submit(generate_tts_response, response, tts_choice)
        audio_path = tts_future.result()
        return audio_path

import re

def clean_response(response_text):
    # Remove system and user tags
    response_text = re.sub(r'<\|system\|>.*?<\|end\|>', '', response_text, flags=re.DOTALL)
    response_text = re.sub(r'<\|user\|>.*?<\|end\|>', '', response_text, flags=re.DOTALL)
    response_text = re.sub(r'<\|assistant\|>', '', response_text, flags=re.DOTALL)

    # Clean up the text by removing extra whitespace
    cleaned_response = response_text.strip()
    cleaned_response = re.sub(r'\s+', ' ', cleaned_response)

    # Ensure the response is conversational and organized
    cleaned_response = cleaned_response.replace('1.', '\n1.').replace('2.', '\n2.').replace('3.', '\n3.').replace('4.', '\n4.').replace('5.', '\n5.')

    return cleaned_response




import traceback

def generate_answer(message, choice, retrieval_mode, selected_model):
    logging.debug(f"generate_answer called with choice: {choice}, retrieval_mode: {retrieval_mode}, and selected_model: {selected_model}")

    # Logic for disabling options for Phi-3.5
    if selected_model == "Phi-3.5":
        choice = None
        retrieval_mode = None

    try:
        # Select the appropriate template based on the choice
        if choice == "Details":
            prompt_template = QA_CHAIN_PROMPT_1
        elif choice == "Conversational":
            prompt_template = QA_CHAIN_PROMPT_2
        else:
            prompt_template = QA_CHAIN_PROMPT_1  # Fallback to template1

        # Handle hotel-related queries
        if "hotel" in message.lower() or "hotels" in message.lower() and "birmingham" in message.lower():
            logging.debug("Handling hotel-related query")
            response = fetch_google_hotels()
            logging.debug(f"Hotel response: {response}")
            return response, extract_addresses(response)

        # Handle restaurant-related queries
        if "restaurant" in message.lower() or "restaurants" in message.lower() and "birmingham" in message.lower():
            logging.debug("Handling restaurant-related query")
            response = fetch_yelp_restaurants()
            logging.debug(f"Restaurant response: {response}")
            return response, extract_addresses(response)

        # Handle flight-related queries
        if "flight" in message.lower() or "flights" in message.lower() and "birmingham" in message.lower():
            logging.debug("Handling flight-related query")
            response = fetch_google_flights()
            logging.debug(f"Flight response: {response}")
            return response, extract_addresses(response)

        # Retrieval-based response
        if retrieval_mode == "VDB":
            logging.debug("Using VDB retrieval mode")
            if selected_model == chat_model:
                logging.debug("Selected model: GPT-4o")
                retriever = gpt_retriever
                context = retriever.get_relevant_documents(message)
                logging.debug(f"Retrieved context: {context}")

                prompt = prompt_template.format(context=context, question=message)
                logging.debug(f"Generated prompt: {prompt}")

                qa_chain = RetrievalQA.from_chain_type(
                    llm=chat_model,
                    chain_type="stuff",
                    retriever=retriever,
                    chain_type_kwargs={"prompt": prompt_template}
                )
                response = qa_chain({"query": message})
                logging.debug(f"GPT-4o response: {response}")
                return response['result'], extract_addresses(response['result'])

            elif selected_model == phi_pipe:
                logging.debug("Selected model: Phi-3.5")
                retriever = phi_retriever
                context_documents = retriever.get_relevant_documents(message)
                context = "\n".join([doc.page_content for doc in context_documents])
                logging.debug(f"Retrieved context for Phi-3.5: {context}")

                # Use the correct template variable
                prompt = phi_custom_template.format(context=context, question=message)
                logging.debug(f"Generated Phi-3.5 prompt: {prompt}")

                response = selected_model(prompt, **{
                    "max_new_tokens": 400,
                    "return_full_text": True,
                    "temperature": 0.7,
                    "do_sample": True,
                })

                if response:
                    generated_text = response[0]['generated_text']
                    logging.debug(f"Phi-3.5 Response: {generated_text}")
                    cleaned_response = clean_response(generated_text)
                    return cleaned_response, extract_addresses(cleaned_response)
                else:
                    logging.error("Phi-3.5 did not return any response.")
                    return "No response generated.", []

        elif retrieval_mode == "KGF":
            logging.debug("Using KGF retrieval mode")
            response = chain_neo4j.invoke({"question": message})
            logging.debug(f"KGF response: {response}")
            return response, extract_addresses(response)
        else:
            logging.error("Invalid retrieval mode selected.")
            return "Invalid retrieval mode selected.", []

    except Exception as e:
        logging.error(f"Error in generate_answer: {str(e)}")
        logging.error(traceback.format_exc())
        return "Sorry, I encountered an error while processing your request.", []




def add_message(history, message):
    history.append((message, None))
    return history, gr.Textbox(value="", interactive=True, show_label=False)

def print_like_dislike(x: gr.LikeData):
    print(x.index, x.value, x.liked)

def extract_addresses(response):
    if not isinstance(response, str):
        response = str(response)
    address_patterns = [
        r'([A-Z].*,\sBirmingham,\sAL\s\d{5})',
        r'(\d{4}\s.*,\sBirmingham,\sAL\s\d{5})',
        r'([A-Z].*,\sAL\s\d{5})',
        r'([A-Z].*,.*\sSt,\sBirmingham,\sAL\s\d{5})',
        r'([A-Z].*,.*\sStreets,\sBirmingham,\sAL\s\d{5})',
        r'(\d{2}.*\sStreets)',
        r'([A-Z].*\s\d{2},\sBirmingham,\sAL\s\d{5})',
        r'([a-zA-Z]\s Birmingham)',
        r'([a-zA-Z].*,\sBirmingham,\sAL)',
        r'(.*),(Birmingham, AL,USA)$'
        r'(^Birmingham,AL$)',
        r'((.*)(Stadium|Field),.*,\sAL$)',
        r'((.*)(Stadium|Field),.*,\sFL$)',
        r'((.*)(Stadium|Field),.*,\sMS$)',
        r'((.*)(Stadium|Field),.*,\sAR$)',
        r'((.*)(Stadium|Field),.*,\sKY$)',
        r'((.*)(Stadium|Field),.*,\sTN$)',
        r'((.*)(Stadium|Field),.*,\sLA$)',
        r'((.*)(Stadium|Field),.*,\sFL$)'

    ]
    addresses = []
    for pattern in address_patterns:
        addresses.extend(re.findall(pattern, response))
    return addresses

all_addresses = []

def generate_map(location_names):
    global all_addresses
    all_addresses.extend(location_names)

    api_key = os.environ['GOOGLEMAPS_API_KEY']
    gmaps = GoogleMapsClient(key=api_key)

    m = folium.Map(location=[33.5175, -86.809444], zoom_start=12)

    for location_name in all_addresses:
        geocode_result = gmaps.geocode(location_name)
        if geocode_result:
            location = geocode_result[0]['geometry']['location']
            folium.Marker(
                [location['lat'], location['lng']],
                tooltip=f"{geocode_result[0]['formatted_address']}"
            ).add_to(m)

    map_html = m._repr_html_()
    return map_html


def fetch_local_news():
    api_key = os.environ['SERP_API']
    url = f'https://serpapi.com/search.json?engine=google_news&q=birmingham headline&api_key={api_key}'
    response = requests.get(url)
    if response.status_code == 200:
        results = response.json().get("news_results", [])
        news_html = """
        <h2 style="font-family: 'Georgia', serif; color: #ff0000; background-color: #f8f8f8; padding: 10px; border-radius: 10px;">Birmingham Today</h2>
        <style>
            .news-item {
                font-family: 'Verdana', sans-serif;
                color: #333;
                background-color: #f0f8ff;
                margin-bottom: 15px;
                padding: 10px;
                border-radius: 5px;
                transition: box-shadow 0.3s ease, background-color 0.3s ease;
                font-weight: bold;
            }
            .news-item:hover {
                box-shadow: 0 4px 8px rgba(0, 0, 0, 0.1);
                background-color: #e6f7ff;
            }
            .news-item a {
                color: #1E90FF;
                text-decoration: none;
                font-weight: bold;
            }
            .news-item a:hover {
                text-decoration: underline;
            }
            .news-preview {
                position: absolute;
                display: none;
                border: 1px solid #ccc;
                border-radius: 5px;
                box-shadow: 0 2px 4px rgba(0, 0, 0, 0.2);
                background-color: white;
                z-index: 1000;
                max-width: 300px;
                padding: 10px;
                font-family: 'Verdana', sans-serif;
                color: #333;
            }
        </style>
        <script>
            function showPreview(event, previewContent) {
                var previewBox = document.getElementById('news-preview');
                previewBox.innerHTML = previewContent;
                previewBox.style.left = event.pageX + 'px';
                previewBox.style.top = event.pageY + 'px';
                previewBox.style.display = 'block';
            }
            function hidePreview() {
                var previewBox = document.getElementById('news-preview');
                previewBox.style.display = 'none';
            }
        </script>
        <div id="news-preview" class="news-preview"></div>
        """
        for index, result in enumerate(results[:7]):
            title = result.get("title", "No title")
            link = result.get("link", "#")
            snippet = result.get("snippet", "")
            news_html += f"""
            <div class="news-item" onmouseover="showPreview(event, '{snippet}')" onmouseout="hidePreview()">
                <a href='{link}' target='_blank'>{index + 1}. {title}</a>
                <p>{snippet}</p>
            </div>
            """
        return news_html
    else:
        return "<p>Failed to fetch local news</p>"

import numpy as np
import torch
from transformers import pipeline, AutoModelForSpeechSeq2Seq, AutoProcessor

model_id = 'openai/whisper-large-v3'
device = "cuda:0" if torch.cuda.is_available() else "cpu"
torch_dtype = torch.float16 if torch.cuda.is_available() else torch.float32
model = AutoModelForSpeechSeq2Seq.from_pretrained(model_id, torch_dtype=torch_dtype).to(device)
processor = AutoProcessor.from_pretrained(model_id)

pipe_asr = pipeline("automatic-speech-recognition", model=model, tokenizer=processor.tokenizer, feature_extractor=processor.feature_extractor, max_new_tokens=128, chunk_length_s=15, batch_size=16, torch_dtype=torch_dtype, device=device, return_timestamps=True)

base_audio_drive = "/data/audio"

#Normal Code with sample rate is 44100 Hz

def transcribe_function(stream, new_chunk):
    try:
        sr, y = new_chunk[0], new_chunk[1]
    except TypeError:
        print(f"Error chunk structure: {type(new_chunk)}, content: {new_chunk}")
        return stream, "", None

    y = y.astype(np.float32) / np.max(np.abs(y))

    if stream is not None:
        stream = np.concatenate([stream, y])
    else:
        stream = y

    result = pipe_asr({"array": stream, "sampling_rate": sr}, return_timestamps=False)

    full_text = result.get("text","")

    return stream, full_text, result







def update_map_with_response(history):
    if not history:
        return ""
    response = history[-1][1]
    addresses = extract_addresses(response)
    return generate_map(addresses)

def clear_textbox():
    return ""

def show_map_if_details(history, choice):
    if choice in ["Details", "Conversational"]:
        return gr.update(visible=True), update_map_with_response(history)
    else:
        return gr.update(visible(False), "")








def generate_audio_elevenlabs(text):
    XI_API_KEY = os.environ['ELEVENLABS_API']
    VOICE_ID = 'd9MIrwLnvDeH7aZb61E9'
    tts_url = f"https://api.elevenlabs.io/v1/text-to-speech/{VOICE_ID}/stream"
    headers = {
        "Accept": "application/json",
        "xi-api-key": XI_API_KEY
    }
    data = {
        "text": str(text),
        "model_id": "eleven_multilingual_v2",
        "voice_settings": {
            "stability": 1.0,
            "similarity_boost": 0.0,
            "style": 0.60,
            "use_speaker_boost": False
        }
    }
    response = requests.post(tts_url, headers=headers, json=data, stream=True)
    if response.ok:
        audio_segments = []
        with tempfile.NamedTemporaryFile(delete=False, suffix=".mp3") as f:
            for chunk in response.iter_content(chunk_size=1024):
                if chunk:
                    f.write(chunk)
                    audio_segments.append(chunk)
            temp_audio_path = f.name

        # Combine all audio chunks into a single file
        combined_audio = AudioSegment.from_file(temp_audio_path, format="mp3")
        combined_audio_path = os.path.join(tempfile.gettempdir(), "elevenlabs_combined_audio.mp3")
        combined_audio.export(combined_audio_path, format="mp3")

        logging.debug(f"Audio saved to {combined_audio_path}")
        return combined_audio_path
    else:
        logging.error(f"Error generating audio: {response.text}")
        return None




# chunking audio and then Process

import concurrent.futures
import tempfile
import os
import numpy as np
import logging
from queue import Queue
from threading import Thread
from scipy.io.wavfile import write as write_wav
from parler_tts import ParlerTTSForConditionalGeneration, ParlerTTSStreamer
from transformers import AutoTokenizer

# Ensure your device is set to CUDA
device = "cuda:0" if torch.cuda.is_available() else "cpu"

repo_id = "parler-tts/parler-tts-mini-v1"

def generate_audio_parler_tts(text):
    description = "A female speaker delivers a slightly expressive and animated speech with a moderate speed and pitch. The recording is of very high quality, with the speaker's voice sounding clear and very close up."
    chunk_size_in_s = 0.5

    # Initialize the tokenizer and model
    parler_tokenizer = AutoTokenizer.from_pretrained(repo_id)
    parler_model = ParlerTTSForConditionalGeneration.from_pretrained(repo_id).to(device)
    sampling_rate = parler_model.audio_encoder.config.sampling_rate
    frame_rate = parler_model.audio_encoder.config.frame_rate

    def generate(text, description, play_steps_in_s=0.5):
        play_steps = int(frame_rate * play_steps_in_s)
        streamer = ParlerTTSStreamer(parler_model, device=device, play_steps=play_steps)

        inputs = parler_tokenizer(description, return_tensors="pt").to(device)
        prompt = parler_tokenizer(text, return_tensors="pt").to(device)

        generation_kwargs = dict(
            input_ids=inputs.input_ids,
            prompt_input_ids=prompt.input_ids,
            attention_mask=inputs.attention_mask,
            prompt_attention_mask=prompt.attention_mask,
            streamer=streamer,
            do_sample=True,
            temperature=1.0,
            min_new_tokens=10,
        )

        thread = Thread(target=parler_model.generate, kwargs=generation_kwargs)
        thread.start()

        for new_audio in streamer:
            if new_audio.shape[0] == 0:
                break
            # Save or process each audio chunk as it is generated
            yield sampling_rate, new_audio

    audio_segments = []
    for (sampling_rate, audio_chunk) in generate(text, description, chunk_size_in_s):
        audio_segments.append(audio_chunk)

        temp_audio_path = os.path.join(tempfile.gettempdir(), f"parler_tts_audio_chunk_{len(audio_segments)}.wav")
        write_wav(temp_audio_path, sampling_rate, audio_chunk.astype(np.float32))
        logging.debug(f"Saved chunk to {temp_audio_path}")


    # Combine all the audio chunks into one audio file
    combined_audio = np.concatenate(audio_segments)
    combined_audio_path = os.path.join(tempfile.gettempdir(), "parler_tts_combined_audio_stream.wav")

    write_wav(combined_audio_path, sampling_rate, combined_audio.astype(np.float32))

    logging.debug(f"Combined audio saved to {combined_audio_path}")
    return combined_audio_path


def fetch_local_events():
    api_key = os.environ['SERP_API']
    url = f'https://serpapi.com/search.json?engine=google_events&q=Events+in+Birmingham&hl=en&gl=us&api_key={api_key}'
    response = requests.get(url)
    if response.status_code == 200:
        events_results = response.json().get("events_results", [])
        events_html = """
        <h2 style="font-family: 'Georgia', serif; color: #ff0000; background-color: #f8f8f8; padding: 10px; border-radius: 10px;">Local Events</h2>
        <style>
            table {
                font-family: 'Verdana', sans-serif;
                color: #333;
                border-collapse: collapse;
                width: 100%;
            }
            th, td {
                border: 1px solid #fff !important;
                padding: 8px;
            }
            th {
                background-color: #f2f2f2;
                color: #333;
                text-align: left;
            }
            tr:hover {
                background-color: #f5f5f5;
            }
            .event-link {
                color: #1E90FF;
                text-decoration: none;
            }
            .event-link:hover {
                text-decoration: underline;
            }
        </style>
        <table>
            <tr>
                <th>Title</th>
                <th>Date and Time</th>
                <th>Location</th>
            </tr>
        """
        for event in events_results:
            title = event.get("title", "No title")
            date_info = event.get("date", {})
            date = f"{date_info.get('start_date', '')} {date_info.get('when', '')}".replace("{", "").replace("}", "")
            location = event.get("address", "No location")
            if isinstance(location, list):
                location = " ".join(location)
            location = location.replace("[", "").replace("]", "")
            link = event.get("link", "#")
            events_html += f"""
            <tr>
                <td><a class='event-link' href='{link}' target='_blank'>{title}</a></td>
                <td>{date}</td>
                <td>{location}</td>
            </tr>
            """
        events_html += "</table>"
        return events_html
    else:
        return "<p>Failed to fetch local events</p>"

def get_weather_icon(condition):
    condition_map = {
        "Clear": "c01d",
        "Partly Cloudy": "c02d",
        "Cloudy": "c03d",
        "Overcast": "c04d",
        "Mist": "a01d",
        "Patchy rain possible": "r01d",
        "Light rain": "r02d",
        "Moderate rain": "r03d",
        "Heavy rain": "r04d",
        "Snow": "s01d",
        "Thunderstorm": "t01d",
        "Fog": "a05d",
    }
    return condition_map.get(condition, "c04d")

def fetch_local_weather():
    try:
        api_key = os.environ['WEATHER_API']
        url = f'https://weather.visualcrossing.com/VisualCrossingWebServices/rest/services/timeline/birmingham?unitGroup=metric&include=events%2Calerts%2Chours%2Cdays%2Ccurrent&key={api_key}'
        response = requests.get(url)
        response.raise_for_status()
        jsonData = response.json()

        current_conditions = jsonData.get("currentConditions", {})
        temp_celsius = current_conditions.get("temp", "N/A")

        if temp_celsius != "N/A":
            temp_fahrenheit = int((temp_celsius * 9/5) + 32)
        else:
            temp_fahrenheit = "N/A"

        condition = current_conditions.get("conditions", "N/A")
        humidity = current_conditions.get("humidity", "N/A")

        weather_html = f"""
        <div class="weather-theme">
            <h2 style="font-family: 'Georgia', serif; color: #ff0000; background-color: #f8f8f8; padding: 10px; border-radius: 10px;">Local Weather</h2>
            <div class="weather-content">
                <div class="weather-icon">
                    <img src="https://www.weatherbit.io/static/img/icons/{get_weather_icon(condition)}.png" alt="{condition}" style="width: 100px; height: 100px;">
                </div>
                <div class="weather-details">
                    <p style="font-family: 'Verdana', sans-serif; color: #333; font-size: 1.2em;">Temperature: {temp_fahrenheit}°F</p>
                    <p style="font-family: 'Verdana', sans-serif; color: #333; font-size: 1.2em;">Condition: {condition}</p>
                    <p style="font-family: 'Verdana', sans-serif; color: #333; font-size: 1.2em;">Humidity: {humidity}%</p>
                </div>
            </div>
        </div>
        <style>
            .weather-theme {{
                animation: backgroundAnimation 10s infinite alternate;
                border-radius: 10px;
                padding: 10px;
                margin-bottom: 15px;
                background: linear-gradient(45deg, #ffcc33, #ff6666, #ffcc33, #ff6666);
                background-size: 400% 400%;
                box-shadow: 0 4px 8px rgba(0, 0, 0, 0.1);
                transition: box-shadow 0.3s ease, background-color 0.3s ease;
            }}
            .weather-theme:hover {{
                box-shadow: 0 8px 16px rgba(0, 0, 0, 0.2);
                background-position: 100% 100%;
            }}
            @keyframes backgroundAnimation {{
                0% {{ background-position: 0% 50%; }}
                100% {{ background-position: 100% 50%; }}
            }}
            .weather-content {{
                display: flex;
                align-items: center;
            }}
            .weather-icon {{
                flex: 1;
            }}
            .weather-details {{
                flex 3;
            }}
        </style>
        """
        return weather_html
    except requests.exceptions.RequestException as e:
        return f"<p>Failed to fetch local weather: {e}</p>"


def handle_retrieval_mode_change(choice):
    if choice == "KGF":
        return gr.update(interactive=False), gr.update(interactive=False)
    else:
        return gr.update(interactive=True), gr.update(interactive=True)

def handle_model_choice_change(selected_model):
    if selected_model == "Phi-3.5":
        # Disable retrieval mode and select style when Phi-3.5 is selected
        return gr.update(interactive=False), gr.update(interactive=False), gr.update(interactive=False)
    elif selected_model == "GPT-4o":
        # Enable retrieval mode and select style for GPT-4o
        return gr.update(interactive=True), gr.update(interactive=True), gr.update(interactive=True)
    else:
        # Default case: allow interaction
        return gr.update(interactive=True), gr.update(interactive=True), gr.update(interactive=True)




def format_restaurant_hotel_info(name, link, location, phone, rating, reviews, snippet):
    return f"""
    {name}
    - Link: {link}
    - Location: {location}
    - Contact No: {phone}
    - Rating: {rating} stars ({reviews} reviews)
    - Snippet: {snippet}
    """

def fetch_yelp_restaurants():
    # Introductory prompt for restaurants
    intro_prompt = "Here are some of the top-rated restaurants in Birmingham, Alabama. I hope these suggestions help you find the perfect place to enjoy your meal:"

    params = {
        "engine": "yelp",
        "find_desc": "Restaurant",
        "find_loc": "Birmingham, AL, USA",
        "api_key": os.getenv("SERP_API")
    }

    search = GoogleSearch(params)
    results = search.get_dict()
    organic_results = results.get("organic_results", [])

    response_text = f"{intro_prompt}\n"

    for result in organic_results[:5]:  # Limiting to top 5 restaurants
        name = result.get("title", "No name")
        rating = result.get("rating", "No rating")
        reviews = result.get("reviews", "No reviews")
        phone = result.get("phone", "Not Available")
        snippet = result.get("snippet", "Not Available")
        location = f"{name}, Birmingham, AL,USA"
        link = result.get("link", "#")

        response_text += format_restaurant_hotel_info(name, link, location, phone, rating, reviews, snippet)


    return response_text






def format_hotel_info(name, link, location, rate_per_night, total_rate, description, check_in_time, check_out_time, amenities):
    return f"""
    {name}
    - Link: {link}
    - Location: {location}
    - Rate per Night: {rate_per_night} (Before taxes/fees: {total_rate})
    - Check-in Time: {check_in_time}
    - Check-out Time: {check_out_time}
    - Amenities: {amenities}
    - Description: {description}
    """

def fetch_google_hotels(query="Birmingham Hotel", check_in=current_date1, check_out="2024-09-02", adults=2):
    # Introductory prompt for hotels
    intro_prompt = "Here are some of the best hotels in Birmingham, Alabama, for your stay. Each of these options offers a unique experience, whether you're looking for luxury, comfort, or convenience:"

    params = {
        "engine": "google_hotels",
        "q": query,
        "check_in_date": check_in,
        "check_out_date": check_out,
        "adults": str(adults),
        "currency": "USD",
        "gl": "us",
        "hl": "en",
        "api_key": os.getenv("SERP_API")
    }

    search = GoogleSearch(params)
    results = search.get_dict()
    hotel_results = results.get("properties", [])

    hotel_info = f"{intro_prompt}\n"
    for hotel in hotel_results[:5]:  # Limiting to top 5 hotels
        name = hotel.get('name', 'No name')
        description = hotel.get('description', 'No description')
        link = hotel.get('link', '#')
        check_in_time = hotel.get('check_in_time', 'N/A')
        check_out_time = hotel.get('check_out_time', 'N/A')
        rate_per_night = hotel.get('rate_per_night', {}).get('lowest', 'N/A')
        before_taxes_fees = hotel.get('rate_per_night', {}).get('before_taxes_fees', 'N/A')
        total_rate = hotel.get('total_rate', {}).get('lowest', 'N/A')
        amenities = ", ".join(hotel.get('amenities', [])) if hotel.get('amenities') else "Not Available"

        location = f"{name}, Birmingham, AL,USA"

        hotel_info += format_hotel_info(
            name,
            link,
            location,
            rate_per_night,
            total_rate,
            description,
            check_in_time,
            check_out_time,
            amenities
        )


    return hotel_info




def format_flight_info(flight_number, departure_airport, departure_time, arrival_airport, arrival_time, duration, airplane):
    return f"""
    Flight {flight_number}
    - Departure: {departure_airport} at {departure_time}
    - Arrival: {arrival_airport} at {arrival_time}
    - Duration: {duration} minutes
    - Airplane: {airplane}
    """

def fetch_google_flights(departure_id="JFK", arrival_id="BHM", outbound_date=current_date1, return_date="2024-08-20"):
    # Introductory prompt for flights
    intro_prompt = "Here are some available flights from JFK to Birmingham, Alabama. These options provide a range of times and durations to fit your travel needs:"

    params = {
        "engine": "google_flights",
        "departure_id": departure_id,
        "arrival_id": arrival_id,
        "outbound_date": outbound_date,
        "return_date": return_date,
        "currency": "USD",
        "hl": "en",
        "api_key": os.getenv("SERP_API")
    }

    search = GoogleSearch(params)
    results = search.get_dict()

    # Extract flight details from the results
    best_flights = results.get('best_flights', [])
    flight_info = f"{intro_prompt}\n"

    # Process each flight in the best_flights list
    for i, flight in enumerate(best_flights, start=1):
        for segment in flight.get('flights', []):
            departure_airport = segment.get('departure_airport', {}).get('name', 'Unknown Departure Airport')
            departure_time = segment.get('departure_airport', {}).get('time', 'Unknown Time')
            arrival_airport = segment.get('arrival_airport', {}).get('name', 'Unknown Arrival Airport')
            arrival_time = segment.get('arrival_airport', {}).get('time', 'Unknown Time')
            duration = segment.get('duration', 'Unknown Duration')
            airplane = segment.get('airplane', 'Unknown Airplane')

            # Format the flight segment details
            flight_info += format_flight_info(
                flight_number=i,
                departure_airport=departure_airport,
                departure_time=departure_time,
                arrival_airport=arrival_airport,
                arrival_time=arrival_time,
                duration=duration,
                airplane=airplane
            )


    return flight_info




with gr.Blocks(theme='Pijush2023/scikit-learn-pijush') as demo:
    with gr.Row():
        with gr.Column():
            state = gr.State()

            chatbot = gr.Chatbot([], elem_id="RADAR:Channel 94.1", bubble_full_width=False)
            choice = gr.Radio(label="Select Style", choices=["Details", "Conversational"], value="Conversational")
            retrieval_mode = gr.Radio(label="Retrieval Mode", choices=["VDB", "KGF"], value="VDB")
            model_choice = gr.Dropdown(label="Choose Model", choices=["GPT-4o", "Phi-3.5"], value="GPT-4o")

            # Link the dropdown change to handle_model_choice_change
            model_choice.change(fn=handle_model_choice_change, inputs=model_choice, outputs=[retrieval_mode, choice, choice])

            gr.Markdown("<h1 style='color: red;'>Talk to RADAR</h1>", elem_id="voice-markdown")

            chat_input = gr.Textbox(show_copy_button=True, interactive=True, show_label=False, label="ASK Radar !!!", placeholder="Hey Radar...!!")
            tts_choice = gr.Radio(label="Select TTS System", choices=["Alpha", "Beta"], value="Alpha")
            retriever_button = gr.Button("Retriever")

            clear_button = gr.Button("Clear")
            clear_button.click(lambda: [None, None], outputs=[chat_input, state])

            gr.Markdown("<h1 style='color: red;'>Radar Map</h1>", elem_id="Map-Radar")
            location_output = gr.HTML()
            audio_output = gr.Audio(interactive=False, autoplay=True)

            def stop_audio():
                audio_output.stop()
                return None


            # retriever_sequence = (
            #     retriever_button.click(fn=stop_audio, inputs=[], outputs=[audio_output], api_name="api_stop_audio_recording")
            #     .then(fn=add_message, inputs=[chatbot, chat_input], outputs=[chatbot, chat_input], api_name="api_addprompt_chathistory")
            #     .then(fn=bot, inputs=[chatbot, choice, tts_choice, retrieval_mode, model_choice], outputs=[chatbot, audio_output], api_name="api_askchatbot_then_generateaudio")
            #     .then(fn=show_map_if_details, inputs=[chatbot, choice], outputs=[location_output, location_output], api_name="api_show_map_details")
            #     .then(fn=clear_textbox, inputs=[], outputs=[chat_input],api_name="api_clear_textbox")
            # )

            retriever_sequence = (
                retriever_button.click(fn=stop_audio, inputs=[], outputs=[audio_output], api_name="api_stop_audio_recording")
                .then(fn=add_message, inputs=[chatbot, chat_input], outputs=[chatbot, chat_input], api_name="api_addprompt_chathistory")
                # First, generate the bot response
                .then(fn=generate_bot_response, inputs=[chatbot, choice, retrieval_mode, model_choice], outputs=[chatbot], api_name="api_generate_bot_response")
                # Then, generate the TTS response based on the bot's response
                .then(fn=generate_tts_response, inputs=[chatbot, tts_choice], outputs=[audio_output], api_name="api_generate_tts_response")
                .then(fn=show_map_if_details, inputs=[chatbot, choice], outputs=[location_output, location_output], api_name="api_show_map_details")
                .then(fn=clear_textbox, inputs=[], outputs=[chat_input], api_name="api_clear_textbox")
            )






            # chat_input.submit(fn=stop_audio, inputs=[], outputs=[audio_output],api_name="api_stop_audio_recording")
            # chat_input.submit(fn=add_message, inputs=[chatbot, chat_input], outputs=[chatbot, chat_input], api_name="api_addprompt_chathistory").then(
            #     fn=bot, inputs=[chatbot, choice, tts_choice, retrieval_mode, model_choice], outputs=[chatbot, audio_output], api_name="api_askchatbot_then_generateaudio"
            # ).then(
            #     fn=show_map_if_details, inputs=[chatbot, choice], outputs=[location_output, location_output], api_name="api_show_map_details"
            # ).then(
            #     fn=clear_textbox, inputs=[], outputs=[chat_input],api_name="api_clear_textbox"
            # )

            chat_input.submit(fn=stop_audio, inputs=[], outputs=[audio_output], api_name="api_stop_audio_recording").then(
                fn=add_message, inputs=[chatbot, chat_input], outputs=[chatbot, chat_input], api_name="api_addprompt_chathistory"
            ).then(
                # First, generate the bot response
                fn=generate_bot_response, inputs=[chatbot, choice, retrieval_mode, model_choice], outputs=[chatbot], api_name="api_generate_bot_response"
            ).then(
                # Then, generate the TTS response based on the bot's response
                fn=generate_tts_response, inputs=[chatbot, tts_choice], outputs=[audio_output], api_name="api_generate_tts_response"
            ).then(
                fn=show_map_if_details, inputs=[chatbot, choice], outputs=[location_output, location_output], api_name="api_show_map_details"
            ).then(
                fn=clear_textbox, inputs=[], outputs=[chat_input], api_name="api_clear_textbox"
            )







            audio_input = gr.Audio(sources=["microphone"], streaming=True, type='numpy', every=0.1)
            audio_input.stream(transcribe_function, inputs=[state, audio_input], outputs=[state, chat_input], api_name="api_voice_to_text")

        with gr.Column():
            weather_output = gr.HTML(value=fetch_local_weather())
            news_output = gr.HTML(value=fetch_local_news())
            events_output = gr.HTML(value=fetch_local_events())

demo.queue()
demo.launch(show_error=True)
